In [ ]:
import pandas as pd
import numpy as np
import seaborn as sns

#Preprocesamiento

In [ ]:
df = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/spotify/charts.csv')
#Conversion de formato de alguna variable
df['date'] = pd.DatetimeIndex(df['date'])

#Filtros al dataset maestro
df = df[(df['chart'] == 'top200')
       &(df.date >= '2020-01-01')
       &(df.date <= '2021-12-31')
       &(~df.region.isin(['Global']))]

#Convertir a millones
df['streams'] = df['streams']/1000000

<ipython-input-2-422349504e3b>:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['streams'] = df['streams']/1000000


In [ ]:
genres = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/spotify/train.csv')
genres = genres.drop_duplicates(subset=['track_name', 'artists'])
genres.to_csv('/content/drive/MyDrive/Colab Notebooks/spotify/genres.csv')

In [ ]:
codes = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/spotify/countries_codes_and_coordinates.csv')

In [ ]:
codes.to_csv('/content/drive/MyDrive/Colab Notebooks/spotify/countries_codes.csv')

In [ ]:
codes[ 'Alpha-2 code'] = codes[ 'Alpha-2 code'].apply(lambda x: x.strip())
codes[ 'Alpha-2 code'] = codes[ 'Alpha-2 code'].apply(lambda x: x[1:-1])

codes[ 'Alpha-3 code'] = codes[ 'Alpha-3 code'].apply(lambda x: x.strip())
codes[ 'Alpha-3 code'] = codes[ 'Alpha-3 code'].apply(lambda x: x[1:-1])

codes[ 'Latitude (average)'] = codes[ 'Latitude (average)'].apply(lambda x: x.strip())
codes[ 'Latitude (average)'] = codes[ 'Latitude (average)'].apply(lambda x: x[1:-1])
codes[ 'Latitude (average)'] = codes[ 'Latitude (average)'].astype('float')

codes[ 'Longitude (average)'] = codes['Longitude (average)'].apply(lambda x: x.strip())
codes[ 'Longitude (average)'] = codes['Longitude (average)'].apply(lambda x: x[1:-1])
codes[ 'Longitude (average)'] = codes['Longitude (average)'].astype('float')

codes = codes[~codes.Country.isin(['United States Minor Outlying Islands'])]

def regioncode(x):
  if len(x.split(" ")) > 1:
    return  x.split(' ')[0] + " " + x.split(' ')[1]
  else:
    return x

codes['Country'] = codes['Country'].apply(regioncode)

<ipython-input-5-e9e9d7e598fa>:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  codes['Country'] = codes['Country'].apply(regioncode)


In [ ]:
df_code = df.merge(codes, how='left', left_on='region', right_on='Country')
df_code[['region',
    'Country']].drop_duplicates(subset=['region',
                                        'Country'])[df_code.Country.isna()]

<ipython-input-6-cdde201284c8>:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  df_code[['region',


region Country
18338  United Arab Emirates     NaN

In [ ]:
# JOIN con tabla externa - Merge con géneros músicales
df_master = df_code.merge(genres,
         how='left',
         left_on=['title', 'artist'],
         right_on=['track_name', 'artists']).dropna()
df_master.shape

(2004526, 36)

In [ ]:
df_master.to_csv("/content/drive/MyDrive/Colab Notebooks/spotify/df_master.csv")

# Análisis

In [1]:
import pandas as pd

df_master = pd.read_csv('/content/drive/MyDrive/Colab Notebooks/spotify/df_master.csv')
df_master['date'] = pd.DatetimeIndex(df_master['date'])

### Géneros más escuchados en el mundo

In [ ]:
df_master.groupby('track_genre').agg({'streams':'sum'}).sort_values(by='streams',
                                                                    ascending=False).head(5)

streams
track_genre              
pop          16713.473283
dance         8577.244023
hip-hop       5075.466714
latino        5051.842699
k-pop         4770.681453

### Países que escuchan más música

In [ ]:
df_master.groupby('region').agg({'streams':'sum'}).sort_values(by='streams', ascending=False).head(10)

streams
region                      
United States   15263.211902
Mexico           4858.707827
United Kingdom   4289.876904
Japan            3120.426745
Indonesia        2905.407991
Australia        2865.307668
Germany          2827.804650
Philippines      2795.346405
India            2712.527922
Brazil           2508.586511

### Canciones más populares

In [ ]:
df_duracion = df_master.sort_values(by=['region','title', 'date']).groupby(['title']).agg({'date':['min', 'max'],
                                                                                      'streams':'sum'}).reset_index()
df_duracion.columns = ['title', 's_first', 's_last', 'streams']
df_duracion['Trend'] = df_duracion.s_last -  df_duracion.s_first
df_duracion['Trend'] = df_duracion['Trend'].apply(lambda x: x.days)

#Metrica para saber cuál tuvo muchos streams y aparte duró mucho tiempo
# Puede haber canciones que tengan muchas reproducciones pero solo quedaron un tiempo
df_duracion['Duracion_streams'] = df_duracion['Trend']*df_duracion['streams']
df_duracion[['title', 'Trend', 'Duracion_streams']].sort_values(by='Duracion_streams', ascending=False).head(10)

title  Trend  Duracion_streams
260     Blinding Lights    730      1.793489e+06
517     Don't Start Now    730      9.690463e+05
1976   Watermelon Sugar    730      9.461389e+05
1685  Someone You Loved    730      8.199220e+05
626             Falling    698      4.976441e+05
1231           Memories    719      4.564051e+05
538            Dynamite    466      4.337988e+05
769          Heat Waves    546      4.161938e+05
1581    Save Your Tears    651      4.147037e+05
2133    drivers license    357      3.890117e+05

### Artistas más escuchados

In [ ]:
df_master.groupby('artist').agg({'streams':'sum'}).sort_values(by='streams', ascending=False).head(10)

streams
artist                     
Olivia Rodrigo  3499.074482
The Weeknd      3349.810075
Bad Bunny       2557.350942
BTS             2436.961112
Billie Eilish   2333.773202
Dua Lipa        2249.109831
Doja Cat        1672.044281
Ed Sheeran      1467.116683
Måneskin        1343.216610
Travis Scott    1313.528452

### Géneros más escuchados por país

In [ ]:
dfgs = df_master.loc[df_master.region.isin(['Argentina',
                         'Mexico',
                         'United States'])].groupby(['region',
                                                     'track_genre']).agg({'streams':'sum'}).reset_index()

dfgs.sort_values(by=['region',
                     'streams'],
                      ascending=False).groupby(['region']).head(3).groupby(['region',
                                                     'track_genre', 'streams']).count()

Empty DataFrame
Columns: []
Index: [(Argentina, latin, 124.952631), (Argentina, latino, 438.351688), (Argentina, pop, 212.938887), (Mexico, latin, 713.291779), (Mexico, latino, 1742.517783), (Mexico, pop, 695.266034), (United States, dance, 1650.404579), (United States, hip-hop, 1829.117494), (United States, pop, 4166.409211)]

In [2]:
import plotly.express as px
import plotly.graph_objects as go

In [3]:
import plotly.express as px

### Análisis de géneros musicales

In [5]:
# Los géneros más populares en forma de lista
glist = df_master.groupby('track_genre').agg({'streams':'sum'}).sort_values(by='streams',
                                                                    ascending=False).head(5).index.to_list()

topgnresdf = df_master[df_master.track_genre.isin(glist)]

In [29]:
px.line(topgnresdf.groupby(['track_genre', 'date']).agg({'streams':'sum'}).reset_index(),
        x = 'date',
        y = 'streams',
        facet_col='track_genre',
        color='track_genre', title='Comportamiento a nivel diario de streams')

In [ ]:
# dayofweek [1, 2, 3, 4, 5, 6, 7]
topgnresdf['week'] = topgnresdf['date'].apply(lambda x : x - pd.to_timedelta(x.dayofweek, unit='D'))

In [31]:
grouped_df = topgnresdf.groupby(['track_genre', 'week']).agg({'streams':'sum'}).reset_index()
px.line(grouped_df,
        x = 'week',
        y = 'streams',
        facet_col='track_genre',
        color='track_genre')

In [27]:
grouped_df = topgnresdf.groupby(['track_genre', 'week']).agg({'streams':'sum'}).reset_index()
px.scatter(grouped_df,
        x = 'week',
        y = 'streams',
        facet_col='track_genre',
        color='track_genre', trendline='ols')


### Distribución de los datos con más danzabilidad


In [28]:
fig = px.histogram(topgnresdf,
             x='danceability',
             facet_col='track_genre', nbins=20)
fig.update_layout(height=400, title='Distribucion de los datos')

In [ ]:
fig = px.box(topgnresdf,
             y='danceability',
             facet_col='track_genre',
             )

fig.update_layout(height=400, title='Distribucion de los datos')

### Distribución del tempo en los distintos géneros

In [ ]:
fig = px.histogram(topgnresdf,
             x='tempo',
             facet_col='track_genre', nbins=20)
fig.update_layout(height=400, title='Distribución de los datos del tempo (bmp)')